In [89]:
import pandas as pd
from sklearn.decomposition import PCA
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import train_test_split
from sklearn.cluster import KMeans, AffinityPropagation
from scipy.spatial.distance import cdist, pdist
import numpy as np
import matplotlib.pyplot as plt
from mplcursors import cursor
%matplotlib qt

## Live synchronization with the simulator with ROS

To display live updates in the social situation simulator when hovering a specific datapoint in the figures, you need to have ROS installed on your system.

For graphs displaying 2 situations at the same time, you need to start a second instance of the simulator with the parameter `--scene-topic=/socialsituation2`.

In [90]:
import rospy
from std_msgs.msg import String
rospy.init_node("sss_analysis")
pub = rospy.Publisher("/socialsituation", String, queue_size=1)
pub2 = rospy.Publisher("/socialsituation2", String, queue_size=1)


In [358]:
#df = pd.read_csv("openai-embeddings.csv",index_col=0)
#df = pd.read_csv("llama2-13B-embeddings-base-names.csv",index_col=0)
#idx_embedding = 5


#df = pd.read_csv("data/situation_1/embeddings-openai-stable-names-variations-egocentric.csv",index_col=0)
#df = pd.read_csv("data/situation_lfe_1/embeddings-openai-stable-names-no-variations-egocentric.csv",index_col=0)
#df = pd.read_csv("data/situation_lfe_1/embeddings-openai-stable-names-variations-egocentric.csv",index_col=0)

#df = pd.read_csv("data/situation_1/embeddings-openai-stable-names-variations-egocentric-context.csv",index_col=0)

df = pd.read_csv("data/situation_lfe_1/embeddings-openai-stable-names-variations-egocentric-context.csv",index_col=0)

idx_embedding = 8

pd.set_option('display.max_colwidth', 50)
df

group  engaged    ts viewed_by viewed_by_name  \
0         0        1   3.0       {A}          Alice   
1         1        1   1.5       {D}         George   
2         1        1   1.5       {D}         George   
3         2        0   2.5       {E}        Matilda   
4         2        0   2.5       {E}        Matilda   
5         2        0   2.0       {E}        Matilda   
6         2        0   2.0       {E}        Matilda   
7         2        0   2.0       {E}        Matilda   
8         2        0   1.5       {E}        Matilda   
9         3        0   0.5       {E}        Matilda   
10        3        0   0.5       {E}        Matilda   
11        3        0   0.5       {E}        Matilda   
12        3        0   0.5       {E}        Matilda   
13        4        1   3.0       {B}         Oliver   
14        4        1   3.0       {B}         Oliver   
15        5        1   2.5       {B}         Oliver   
16        5        1   2.5       {B}         Oliver   
17        5        1   2.5       {B}         Oliver   
18        5        1   2.5       {B}         Oliver   
19        5        1   2.5       {B}         Oliver   
20        5        1   2.5       {B}         Oliver   
21        6        1   3.0       {C}         Phoebe   
22        6        1   3.0       {C}         Phoebe   
23        6        1   3.0       {C}         Phoebe   
24        6        1   3.0       {C}         Phoebe   
25        6        1   2.5       {C}         Phoebe   
26        6        1   2.5       {C}         Phoebe   
27        3        0   0.5       {E}        Matilda   
28        7        0   4.0       {A}          Alice   
29        7        0   4.0       {A}          Alice   
30        8        1   4.0       {D}         George   
31        9        1   5.0       {A}          Alice   
32        9        1   5.0       {A}          Alice   
33        9        1   5.0       {A}          Alice   
34        9        1   5.0       {A}          Alice   
35       10        1   5.0       {E}        Matilda   
36       10        1   5.0       {E}        Matilda   
37       11        1   5.0       {B}         Oliver   
38       11        0   5.0       {B}         Oliver   
39       11        1   5.0       {B}         Oliver   
40       11        0   5.0       {B}         Oliver   
41       11        0   5.0       {B}         Oliver   
42       11        0   5.0       {B}         Oliver   
43        9        1   5.5       {A}          Alice   
44        9        1   5.0       {A}          Alice   
45       12        0   5.5       {E}        Matilda   
46       12        0   5.5       {E}        Matilda   
47       11        0   5.0       {B}         Oliver   
48       11        0   5.0       {B}         Oliver   
49       11        0   5.0       {B}         Oliver   
50       11        0   5.0       {B}         Oliver   
51       13        1   6.0       {A}          Alice   
52       13        1   6.0       {A}          Alice   
53       13        1   6.0       {A}          Alice   
54       13        1   6.0       {A}          Alice   
55       13        1   6.0       {A}          Alice   
56       13        1   6.0       {A}          Alice   
57       11        0   5.0       {B}         Oliver   
58       11        0   5.0       {B}         Oliver   
59       14        0   6.0       {C}         Phoebe   
60       14        0   6.0       {C}         Phoebe   
61       14        0   6.0       {C}         Phoebe   
62       14        0   6.0       {C}         Phoebe   
63       13        1   6.5       {A}          Alice   
64       13        1   6.5       {A}          Alice   
65       13        1   6.5       {A}          Alice   
66       13        0   6.0       {A}          Alice   
67       13        0   6.0       {A}          Alice   
68       13        0   6.0       {A}          Alice   
69       11        1   5.0       {B}         Oliver   
70       11        0   5.0       {B}         Oliver   
71       14        0   6.5       {C}         P

In [359]:
pca_dim=5
pca = PCA(n_components=pca_dim)
PCA_result = pca.fit_transform(df.iloc[:,idx_embedding:])
pca_df = pd.DataFrame(PCA_result,index=df.index)
pca_df

0         1         2         3         4
0    -0.044071  0.101036  0.080538 -0.051601  0.137371
1    -0.079603  0.150630 -0.021498 -0.072881  0.079306
2    -0.077723  0.146036 -0.056359 -0.067728  0.078891
3     0.050578  0.129744 -0.008371  0.039806  0.054157
4     0.089352  0.117053 -0.022329  0.085450  0.054390
5     0.054683  0.125180 -0.054507  0.058858  0.058493
6     0.085395  0.120592 -0.003447  0.077558  0.055114
7     0.054146  0.128060 -0.047022  0.048484  0.061393
8     0.053650  0.129245 -0.015886  0.040901  0.057566
9     0.055530  0.102867 -0.025130 -0.042282  0.021036
10    0.063686  0.093773 -0.052683 -0.033862  0.021500
11    0.055949  0.097525 -0.028188 -0.036024  0.022574
12    0.084905  0.072646 -0.019289 -0.024201  0.001058
13   -0.088084  0.021373  0.136072 -0.076789 -0.015079
14   -0.095724  0.007828  0.138728 -0.073119 -0.017993
15   -0.106238  0.033070  0.032301 -0.023535 -0.005032
16   -0.109284  0.054265 -0.025895 -0.006949  0.016640
17   -0.104080  0.052557  0.016872 -0.021929  0.001140
18   -0.114074  0.028407  0.028700 -0.015651 -0.002345
19   -0.110574  0.021666  0.042248 -0.017254 -0.005428
20   -0.109123  0.058719 -0.021295 -0.016028  0.003386
21   -0.088374  0.024569  0.135090 -0.080173 -0.009037
22   -0.091863  0.026004  0.135978 -0.079873 -0.003305
23   -0.095180  0.012237  0.136241 -0.074136 -0.006615
24   -0.086823  0.030264  0.133278 -0.080075 -0.009608
25   -0.092706  0.022933  0.135949 -0.079120 -0.000335
26   -0.097040  0.005196  0.136983 -0.072911 -0.003719
27    0.088795  0.063324 -0.041201 -0.015941  0.000102
28   -0.104908  0.007927  0.136489  0.013700  0.037195
29   -0.103335  0.034432  0.136872  0.004694  0.050165
30   -0.103287  0.008097  0.141079 -0.057218  0.056545
31   -0.101586  0.032858  0.028304 -0.066551  0.001904
32   -0.106457  0.018618  0.037858 -0.062213  0.003554
33   -0.099182  0.044248  0.020045 -0.068668  0.004294
34   -0.102220  0.046083 -0.017947 -0.061237  0.017262
35   -0.075089  0.152722  0.004104 -0.077728  0.077333
36   -0.076038  0.148017  0.019168 -0.082404  0.070550
37    0.092645  0.028146 -0.001926 -0.032167 -0.044673
38    0.115426  0.028480  0.003318 -0.030362 -0.059567
39    0.120430  0.025616  0.003248 -0.030668 -0.058557
40    0.125754  0.030252  0.007661 -0.027760 -0.057583
41    0.084768  0.019825 -0.001149 -0.028393 -0.056380
42    0.131819  0.022313  0.023838 -0.029705 -0.062432
43   -0.104379  0.047987 -0.017221 -0.064992  0.007882
44   -0.110278  0.013882  0.030996 -0.058946  0.003844
45    0.081699  0.148590 -0.003388 -0.056428  0.050117
46    0.122247  0.146541  0.005180 -0.052247  0.046297
47    0.123904  0.014449  0.010924 -0.022697 -0.058602
48    0.139867  0.002540  0.022467 -0.020723 -0.078711
49    0.128224  0.020180  0.022965 -0.027063 -0.064310
50    0.126998  0.024912  0.010858 -0.027662 -0.061725
51   -0.131406 -0.021634  0.018864  0.051736 -0.016831
52   -0.128461  0.004890 -0.021238  0.066462  0.003907
53   -0.132769 -0.045425  0.030154  0.043385 -0.013221
54   -0.130926 -0.032321  0.016451  0.037391 -0.016817
55   -0.138743 -0.036417 -0.029707  0.069822 -0.020022
56   -0.137095 -0.036977 -0.028136  0.064560 -0.015348
57    0.134814  0.025838  0.016034 -0.028123 -0.062898
58    0.129194  0.000406  0.027619 -0.021090 -0.070901
59   -0.110165  0.042035 -0.037420 -0.049978  0.044018
60   -0.108575  0.048526 -0.033355 -0.047964  0.041715
61   -0.109177  0.033901 -0.072261 -0.042861  0.046171
62   -0.111589  0.019111 -0.072947 -0.034096  0.041092
63   -0.127377 -0.016858  0.017989  0.037602 -0.014777
64   -0.141428 -0.047467 -0.031428  0.081885 -0.013643
65   -0.126647  0.003346 -0.020705  0.063907 -0.006233
66   -0.123425  0.012875 -0.017709  0.063300 -0.006688
67   -0.129521 -0.004711 -0.026235  0.069846 -0.007146
68   -0.128474 -0.002301  0.007414  0.048617 -0.013139
69    0.130047  0.016318  0.023742 -0.024959 -0.056986
70    0.130755 -0.000018  0.022979 -0.020983 -0.072723
71   -0.114690  0.014286 -0.081803 -0.030157  0.04277

In [360]:
PCA_values = np.arange(pca.n_components_) + 1
plt.plot(PCA_values, pca.explained_variance_ratio_, 'o-', linewidth=2, color='blue')
plt.title('Scree Plot')
plt.xlabel('Principal Component')
plt.ylabel('Variance Explained')

Text(33.722222222222214, 0.5, 'Variance Explained')

In [345]:
Z = pca_df.iloc[:,:3].pivot_table(index=0, columns=1, values=2).T.values
Z = np.nan_to_num(Z, copy=True, nan=0.0)

In [346]:
X_unique = np.sort(pca_df[0].unique())
Y_unique = np.sort(pca_df[1].unique())
X, Y = np.meshgrid(X_unique, Y_unique)

In [347]:
groups_df = pca_df.groupby(df["group"]).mean()

In [348]:
def labelize(idx):
    pub.publish(df.iloc[idx]["short_code"])
    return "idx=%s, %s, t=%s\n- " % (idx,df.iloc[idx]["viewed_by_name"],df.iloc[idx]["ts"])  + \
           "\n- ".join(df.iloc[idx]["desc"].split(";"))


plt.figure(figsize=(25,25))

#for i in range(pca_df.shape[0]):
#    plt.annotate(df["group"].tolist()[i], (pca_df[0].tolist()[i], pca_df[1].tolist()[i]))
plt.scatter(pca_df[0], pca_df[1],c=df["group"]%10,cmap="tab10")

c=cursor(hover=True)
c.connect(
    "add", lambda sel: sel.annotation.set_text(labelize(sel.index)))

plt.scatter(groups_df[0], groups_df[1],c=groups_df.index%10,cmap="tab10", s=200)
for i in range(groups_df.shape[0]):
    plt.annotate(groups_df.index[i], (groups_df[0].tolist()[i], groups_df[1].tolist()[i]))
    


## Similarity between different social situations

In [356]:
def label(coord, df):
    d1,d2=coord
    desc1=df.iloc[d1]
    desc2=df.iloc[d2]
    
    pub.publish(desc1["short_code"])
    pub2.publish(desc2["short_code"])
    
    return "➡️ %s, %s, t=%s\n- " % (d1, desc1["viewed_by_name"],desc1["ts"])  + \
           "\n- ".join(desc1["desc"].split(";")) + \
           "\n⬇️ %s, %s, t=%s\n- " % (d2, desc2["viewed_by_name"],desc2["ts"]) + \
           "\n- ".join(desc2["desc"].split(";"))

def plot_similarity_matrix(df, embeddings_idx=0):
    
    similarity = cosine_similarity(df.iloc[:,embeddings_idx:])

    fig, ax = plt.subplots(figsize=(20,20))
    cax = ax.matshow(similarity, interpolation='nearest')
    ax.grid(True)
    plt.title('Social scenes similarity matrix')
    plt.xticks(range(len(group_embeddings)));
    plt.yticks(range(len(group_embeddings)));
    fig.colorbar(cax, ticks=[0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, .75,.8,.85,.90,.95,1])
    c=cursor(hover=True)
    c.connect(
        "add", lambda sel: sel.annotation.set_text(label(sel.index, df)))


In [357]:
group_descs = df.groupby("group")[["desc", "ts", "viewed_by_name", "short_code"]].apply(lambda row:row.iloc[0,:])
group_embeddings = df.groupby("group").mean().iloc[:,2:]
group_df = pd.concat([group_descs,group_embeddings], axis=1)

#plot_similarity_matrix(group_df[group_df["viewed_by_name"]=="Alice"], embeddings_idx=4)
plot_similarity_matrix(group_df, embeddings_idx=4)

Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/matplotlib/backends/backend_qt5.py", line 506, in _draw_idle
    self.draw()
  File "/usr/lib/python3/dist-packages/matplotlib/backends/backend_agg.py", line 388, in draw
    self.figure.draw(self.renderer)
  File "/usr/lib/python3/dist-packages/matplotlib/artist.py", line 38, in draw_wrapper
    return draw(artist, renderer, *args, **kwargs)
  File "/usr/lib/python3/dist-packages/matplotlib/figure.py", line 1708, in draw
    mimage._draw_list_compositing_images(
  File "/usr/lib/python3/dist-packages/matplotlib/image.py", line 135, in _draw_list_compositing_images
    a.draw(renderer)
  File "/usr/lib/python3/dist-packages/matplotlib/artist.py", line 38, in draw_wrapper
    return draw(artist, renderer, *args, **kwargs)
  File "/usr/lib/python3/dist-packages/matplotlib/text.py", line 2365, in draw
    self.arrow_patch.draw(renderer)
  File "/usr/lib/python3/dist-packages/matplotlib/patches.py", line 4312, in dra

## Assessing the quality of the 'variations' clustering

Probably useful to compare difference sentence embeddings.
Here, results with OpenAI sentence embeddings give a Calinski-Harabasz score of ~250.


See also below how well a simple KNN can assign a variation of a scene to its cluster.

In [317]:
group_pca_df = pca_df
group_pca_df["group"] = df["group"]
group_pca_df = pd.merge(group_pca_df, groups_df, left_on="group", right_index=True, suffixes=["","_group"])
group_pca_df

0         1         2         3         4  group   0_group  \
0   -0.019409 -0.026710  0.053117  0.018842 -0.055503      0 -0.042662   
1   -0.070530 -0.029333  0.073071  0.041824 -0.053447      0 -0.042662   
2   -0.026246 -0.050289  0.038233 -0.026342 -0.070938      0 -0.042662   
3   -0.070830 -0.026580  0.064063  0.028895 -0.061359      0 -0.042662   
4   -0.027790 -0.068456  0.047922 -0.013852 -0.068803      0 -0.042662   
94  -0.070635 -0.040218  0.041311  0.039672 -0.036346      0 -0.042662   
95  -0.022020 -0.059768  0.064873  0.021280 -0.052108      0 -0.042662   
153 -0.070424 -0.027773  0.086180  0.043912 -0.054498      0 -0.042662   
154 -0.055583 -0.057854  0.049059  0.023882 -0.038350      0 -0.042662   
213 -0.030797 -0.045287  0.070719  0.013334 -0.062743      0 -0.042662   
282 -0.050456 -0.051912  0.063937 -0.004284 -0.059528      0 -0.042662   
283 -0.056041 -0.034005  0.065939  0.005621 -0.053094      0 -0.042662   
284 -0.034483 -0.073054  0.047357 -0.020139 -0.072820      0 -0.042662   
285 -0.023979 -0.057743  0.036246 -0.033259 -0.079040      0 -0.042662   
435 -0.024127 -0.045766  0.051307 -0.001896 -0.050792      0 -0.042662   
436 -0.029250 -0.058134  0.025604  0.001402 -0.056188      0 -0.042662   
5   -0.000602  0.076423  0.062193 -0.003376 -0.075950      1 -0.035293   
6   -0.067981  0.061236  0.103364  0.000130 -0.026256      1 -0.035293   
7   -0.077422  0.071769  0.093021  0.001150 -0.038344      1 -0.035293   
8   -0.003055  0.046382  0.096698  0.029625 -0.058710      1 -0.035293   
9   -0.023338  0.022757  0.103761 -0.079904 -0.062715      1 -0.035293   
10  -0.011642  0.069902  0.078440 -0.070741 -0.073830      1 -0.035293   
96  -0.035854  0.030088  0.107054 -0.070931 -0.061429      1 -0.035293   
97  -0.082434  0.076852  0.076235  0.027477 -0.060937      1 -0.035293   
98  -0.020917  0.026938  0.105007 -0.071191 -0.056039      1 -0.035293   
99   0.001257  0.061849  0.087724 -0.008348 -0.046696      1 -0.035293   
100 -0.034007  0.061960  0.078946 -0.065810 -0.076922      1 -0.035293   
155 -0.009336  0.031365  0.101234 -0.014310 -0.047894      1 -0.035293   
156 -0.070848  0.048658  0.097381  0.026104 -0.038770      1 -0.035293   
157 -0.029657  0.029540  0.094993 -0.077185 -0.067354      1 -0.035293   
214 -0.034002  0.021018  0.115971 -0.076699 -0.053033      1 -0.035293   
215 -0.067107  0.043359  0.094699  0.013183 -0.051864      1 -0.035293   
216 -0.025579  0.029502  0.094225 -0.063040 -0.057567      1 -0.035293   
286 -0.008264  0.048594  0.093317 -0.051003 -0.053473      1 -0.035293   
287 -0.070049  0.048651  0.110525 -0.012353 -0.032169      1 -0.035293   
288 -0.016637  0.075017  0.064993  0.023641 -0.072409      1 -0.035293   
289 -0.021278  0.059980  0.077914 -0.005712 -0.067391      1 -0.035293   
355 -0.062587  0.044091  0.104404  0.003974 -0.043455      1 -0.035293   
356  0.010513  0.091755  0.056516  0.026231 -0.072631      1 -0.035293   
357 -0.032077  0.060710  0.086738 -0.082381 -0.073009      1 -0.035293   
358 -0.077252  0.079859  0.087321  0.024156 -0.045759      1 -0.035293   
359 -0.047457  0.034381  0.117334 -0.044077 -0.032021      1 -0.035293   
11  -0.033149  0.113957  0.016161  0.023409  0.029498      2 -0.069440   
12  -0.033714  0.091528  0.023610  0.050277  0.001183      2 -0.069440   
13  -0.025322  0.082748  0.026756  0.061824 -0.001194      2 -0.069440   
14  -0.100797  0.113510  0.041851  0.060501  0.066782      2 -0.069440   
15  -0.029221  0.118571  0.018432  0.043883  0.047074      2 -0.069440   
101 -0.103413  0.096600  0.046558  0.069922  0.039132      2 -0.069440   
102 -0.093125  0.088357  0.050835  0.069963  0.028075      2 -0.069440   
103 -0.090465  0.078400  0.055938  0.035207  0.038711      2 -0.069440   
104 -0.049023  0.092038  0.031286  0.019876  0.047518      2 -0.069440   
105 -0.099397  0.095097  0.039293  0.060559  0.032173      2 -0.069440   
158 -0.078913  0.095973  0.041552  0.040636  0.060283      2 -0.069440   
159 -0.091891  0

In [318]:


group_pca_df["dist_to_centre"] = ((group_pca_df[[str(x) for x in range(pca_dim)]] - group_pca_df[["%s_group" % x for x in range(pca_dim)]].values)**2).sum(axis=1) ** 0.5
group_pca_df

0         1         2         3         4  group   0_group  \
0   -0.019409 -0.026710  0.053117  0.018842 -0.055503      0 -0.042662   
1   -0.070530 -0.029333  0.073071  0.041824 -0.053447      0 -0.042662   
2   -0.026246 -0.050289  0.038233 -0.026342 -0.070938      0 -0.042662   
3   -0.070830 -0.026580  0.064063  0.028895 -0.061359      0 -0.042662   
4   -0.027790 -0.068456  0.047922 -0.013852 -0.068803      0 -0.042662   
94  -0.070635 -0.040218  0.041311  0.039672 -0.036346      0 -0.042662   
95  -0.022020 -0.059768  0.064873  0.021280 -0.052108      0 -0.042662   
153 -0.070424 -0.027773  0.086180  0.043912 -0.054498      0 -0.042662   
154 -0.055583 -0.057854  0.049059  0.023882 -0.038350      0 -0.042662   
213 -0.030797 -0.045287  0.070719  0.013334 -0.062743      0 -0.042662   
282 -0.050456 -0.051912  0.063937 -0.004284 -0.059528      0 -0.042662   
283 -0.056041 -0.034005  0.065939  0.005621 -0.053094      0 -0.042662   
284 -0.034483 -0.073054  0.047357 -0.020139 -0.072820      0 -0.042662   
285 -0.023979 -0.057743  0.036246 -0.033259 -0.079040      0 -0.042662   
435 -0.024127 -0.045766  0.051307 -0.001896 -0.050792      0 -0.042662   
436 -0.029250 -0.058134  0.025604  0.001402 -0.056188      0 -0.042662   
5   -0.000602  0.076423  0.062193 -0.003376 -0.075950      1 -0.035293   
6   -0.067981  0.061236  0.103364  0.000130 -0.026256      1 -0.035293   
7   -0.077422  0.071769  0.093021  0.001150 -0.038344      1 -0.035293   
8   -0.003055  0.046382  0.096698  0.029625 -0.058710      1 -0.035293   
9   -0.023338  0.022757  0.103761 -0.079904 -0.062715      1 -0.035293   
10  -0.011642  0.069902  0.078440 -0.070741 -0.073830      1 -0.035293   
96  -0.035854  0.030088  0.107054 -0.070931 -0.061429      1 -0.035293   
97  -0.082434  0.076852  0.076235  0.027477 -0.060937      1 -0.035293   
98  -0.020917  0.026938  0.105007 -0.071191 -0.056039      1 -0.035293   
99   0.001257  0.061849  0.087724 -0.008348 -0.046696      1 -0.035293   
100 -0.034007  0.061960  0.078946 -0.065810 -0.076922      1 -0.035293   
155 -0.009336  0.031365  0.101234 -0.014310 -0.047894      1 -0.035293   
156 -0.070848  0.048658  0.097381  0.026104 -0.038770      1 -0.035293   
157 -0.029657  0.029540  0.094993 -0.077185 -0.067354      1 -0.035293   
214 -0.034002  0.021018  0.115971 -0.076699 -0.053033      1 -0.035293   
215 -0.067107  0.043359  0.094699  0.013183 -0.051864      1 -0.035293   
216 -0.025579  0.029502  0.094225 -0.063040 -0.057567      1 -0.035293   
286 -0.008264  0.048594  0.093317 -0.051003 -0.053473      1 -0.035293   
287 -0.070049  0.048651  0.110525 -0.012353 -0.032169      1 -0.035293   
288 -0.016637  0.075017  0.064993  0.023641 -0.072409      1 -0.035293   
289 -0.021278  0.059980  0.077914 -0.005712 -0.067391      1 -0.035293   
355 -0.062587  0.044091  0.104404  0.003974 -0.043455      1 -0.035293   
356  0.010513  0.091755  0.056516  0.026231 -0.072631      1 -0.035293   
357 -0.032077  0.060710  0.086738 -0.082381 -0.073009      1 -0.035293   
358 -0.077252  0.079859  0.087321  0.024156 -0.045759      1 -0.035293   
359 -0.047457  0.034381  0.117334 -0.044077 -0.032021      1 -0.035293   
11  -0.033149  0.113957  0.016161  0.023409  0.029498      2 -0.069440   
12  -0.033714  0.091528  0.023610  0.050277  0.001183      2 -0.069440   
13  -0.025322  0.082748  0.026756  0.061824 -0.001194      2 -0.069440   
14  -0.100797  0.113510  0.041851  0.060501  0.066782      2 -0.069440   
15  -0.029221  0.118571  0.018432  0.043883  0.047074      2 -0.069440   
101 -0.103413  0.096600  0.046558  0.069922  0.039132      2 -0.069440   
102 -0.093125  0.088357  0.050835  0.069963  0.028075      2 -0.069440   
103 -0.090465  0.078400  0.055938  0.035207  0.038711      2 -0.069440   
104 -0.049023  0.092038  0.031286  0.019876  0.047518      2 -0.069440   
105 -0.099397  0.095097  0.039293  0.060559  0.032173      2 -0.069440   
158 -0.078913  0.095973  0.041552  0.040636  0.060283      2 -0.069440   
159 -0.091891  0

In [319]:
group_dists_df = group_pca_df.groupby("group")["dist_to_centre"].agg([np.mean, np.std])
group_dists_df.plot(kind = "bar", y = "mean", legend = False,
          xerr = "std", title = "Distance to variations' embedding centres")

In [320]:
from sklearn.metrics import silhouette_score

#silhouette_score(df.iloc[:,idx_embedding:],group_pca_df["group"],metric='cosine')
silhouette_score(group_pca_df[[str(x) for x in range(pca_dim)]],group_pca_df["group"])

0.19874506917376664

In [321]:
from sklearn.metrics import calinski_harabasz_score
calinski_harabasz_score(group_pca_df[[str(x) for x in range(pca_dim)]],group_pca_df["group"])


189.0806161788564

## Training a classifier to identify which scene a variation belong to

- train a classifier to recognise variations of situations with a set of names
- try to recognise the same variations, but with different names

In [351]:
# train classifier using full embeddings
X = df.iloc[:,idx_embedding:]

# train classifier using PCA
#X = pca_df

y = df["group"]

In [352]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=2)

In [353]:
neigh = KNeighborsClassifier(n_neighbors=5)
neigh.fit(X_train, y_train)

KNeighborsClassifier()

### Predicting on a subset of the same data

- openai (text-embedding-ada-002): ~83%
- llama2-13B-4bit quantizied: ~46%

- random names, allocentric, openai: ~17%
- random names, egocentric, openai: ~13%
- stable names, egocentric, openai: ~76%
- stable names, egocentric, no prompt context, openai, LFE situations: ~78%
- stable names, egocentric, with prompt context, openai, LFE situations: ~89%


In [354]:
neigh.score(X_test, y_test)

0.8906752411575563

### Predicting on same scene, different names

In [339]:
df_random_names = pd.read_csv("si",index_col=0)

In [340]:
PCA_result = pca.fit_transform(df_random_names.iloc[:,idx_embedding:])
pca_random_names_df = pd.DataFrame(PCA_result,index=df_random_names.index)

In [341]:
neigh.score(df_random_names.iloc[:,idx_embedding:], df_random_names["group"])
#neigh.score(pca_random_names_df, df_random_names["group"])

0.46190476190476193

In [352]:
from sklearn.metrics import confusion_matrix
from sklearn.metrics import ConfusionMatrixDisplay

conf_matrix=confusion_matrix(df_random_names["group"],neigh.predict(df_random_names.iloc[:,idx_embedding:]))

In [ ]:
fig, ax = plt.subplots(figsize=(7.5, 7.5))
ax.matshow(conf_matrix, cmap=plt.cm.Blues, alpha=1)
#for i in range(conf_matrix.shape[0]):
#    for j in range(conf_matrix.shape[1]):
#        ax.text(x=j, y=i,s=conf_matrix[i, j], va='center', ha='center', size='xx-large')


c=cursor(hover=True)

plt.xlabel('Predictions', fontsize=18)
plt.ylabel('Actuals', fontsize=18)
plt.title('Confusion Matrix', fontsize=18)


=> Accuracy: ~45% with 51 classes

## Different scene: computing similarity of situations

In [375]:
sit2 = pd.read_csv("data/situation_lfe_1/embeddings-openai-stable-names-no-variations-egocentric.csv",index_col=0)

group_descs = df.groupby("group")[["desc", "ts", "viewed_by_name", "short_code"]].apply(lambda row:row.iloc[0,:])
group_embeddings = df.groupby("group").mean().iloc[:,2:]
sit1_groups = pd.concat([group_descs,group_embeddings], axis=1)

sit2 = sit2[sit1_groups.columns]


In [376]:
#together=pd.concat([sit1_groups, sit2]).reset_index(drop=True)
together=sit1_groups.append(sit2)
plot_similarity_matrix(together, embeddings_idx=4)


<ipython-input-376-122376a243c0>:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  together=sit1_groups.append(sit2)
Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py", line 216, in process
    func(*args, **kwargs)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 577, in _on_hover_motion_notify
    self._on_select_event(event)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 625, in _on_select_event
    self.add_selection(pi)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 408, in add_selection
    cb(sel)
  File "<ipython-input-356-992ae3f72337>", line 27, in <lambda>
    "add", lambda sel: sel.annotation.set_text(label(sel.index, df)))
TypeError: 'numpy.ndarray' object is not callable
Traceback (

  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 625, in _on_select_event
    self.add_selection(pi)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 408, in add_selection
    cb(sel)
  File "<ipython-input-356-992ae3f72337>", line 27, in <lambda>
    "add", lambda sel: sel.annotation.set_text(label(sel.index, df)))
TypeError: 'numpy.ndarray' object is not callable
Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py", line 216, in process
    func(*args, **kwargs)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 577, in _on_hover_motion_notify
    self._on_select_event(event)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 625, in _on_select_event
    self.add_selection(pi)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages

Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py", line 216, in process
    func(*args, **kwargs)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 577, in _on_hover_motion_notify
    self._on_select_event(event)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 625, in _on_select_event
    self.add_selection(pi)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 408, in add_selection
    cb(sel)
  File "<ipython-input-356-992ae3f72337>", line 27, in <lambda>
    "add", lambda sel: sel.annotation.set_text(label(sel.index, df)))
TypeError: 'numpy.ndarray' object is not callable
Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py", line 216, in process
    func(*args, **kwargs)
  File "/home/severinlemaignan/.local/lib/python3.8/site-package

  File "/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py", line 216, in process
    func(*args, **kwargs)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 577, in _on_hover_motion_notify
    self._on_select_event(event)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 625, in _on_select_event
    self.add_selection(pi)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 408, in add_selection
    cb(sel)
  File "<ipython-input-356-992ae3f72337>", line 27, in <lambda>
    "add", lambda sel: sel.annotation.set_text(label(sel.index, df)))
TypeError: 'numpy.ndarray' object is not callable
Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py", line 216, in process
    func(*args, **kwargs)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 

Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py", line 216, in process
    func(*args, **kwargs)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 577, in _on_hover_motion_notify
    self._on_select_event(event)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 625, in _on_select_event
    self.add_selection(pi)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 408, in add_selection
    cb(sel)
  File "<ipython-input-356-992ae3f72337>", line 27, in <lambda>
    "add", lambda sel: sel.annotation.set_text(label(sel.index, df)))
TypeError: 'numpy.ndarray' object is not callable
Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py", line 216, in process
    func(*args, **kwargs)
  File "/home/severinlemaignan/.local/lib/python3.8/site-package

Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py", line 216, in process
    func(*args, **kwargs)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 577, in _on_hover_motion_notify
    self._on_select_event(event)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 625, in _on_select_event
    self.add_selection(pi)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 408, in add_selection
    cb(sel)
  File "<ipython-input-356-992ae3f72337>", line 27, in <lambda>
    "add", lambda sel: sel.annotation.set_text(label(sel.index, df)))
TypeError: 'numpy.ndarray' object is not callable
Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py", line 216, in process
    func(*args, **kwargs)
  File "/home/severinlemaignan/.local/lib/python3.8/site-package

Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py", line 216, in process
    func(*args, **kwargs)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 577, in _on_hover_motion_notify
    self._on_select_event(event)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 625, in _on_select_event
    self.add_selection(pi)
  File "/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_mplcursors.py", line 408, in add_selection
    cb(sel)
  File "<ipython-input-356-992ae3f72337>", line 27, in <lambda>
    "add", lambda sel: sel.annotation.set_text(label(sel.index, df)))
TypeError: 'numpy.ndarray' object is not callable
Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py", line 216, in process
    func(*args, **kwargs)
  File "/home/severinlemaignan/.local/lib/python3.8/site-package

/home/severinlemaignan/.local/lib/python3.8/site-packages/mplcursors/_pick_info.py:162: UserWarning: Pick support for QuadMesh is missing.
  warnings.warn(f"Pick support for {type(artist).__name__} is missing.")


## Training a classifier to recognise engagement


In [372]:
y = df["engaged"]
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=2)

neigh = KNeighborsClassifier(n_neighbors=3)
neigh.fit(X_train, y_train)

KNeighborsClassifier(n_neighbors=3)

In [373]:
neigh.score(X_test, y_test)

0.7813504823151125

In [374]:
neigh.score(df_random_names.iloc[:,idx_embedding:], df_random_names["engaged"])

NameError: name 'df_random_names' is not defined

### TODO: compare to visual social engagement from hri_engagement

## Clustering social situations

Automatic clustering.
Scene with engagement are plotted with a star. Black dots indicate the 'central situation', eg the know social situation the closest to the clusters' centers.

In [368]:
X = df.iloc[:,idx_embedding:]

clustering = KMeans(n_clusters=8, random_state=1, init='k-means++')
#clustering = AffinityPropagation(random_state=0)

label = clustering.fit_predict(X)
cluster_centers=clustering.cluster_centers_

In [369]:
def closest_situations(embeddings, df, idx_embedding=idx_embedding):
    """ Find closest point from a list of points. """
    return np.array([cdist([emb], df.iloc[:,idx_embedding:],metric="cosine").argmin() for emb in embeddings])

In [370]:
central_situations = closest_situations(cluster_centers, df)

In [371]:
def labelize(idx):
    idx=central_situations[idx]
    return "idx=%s, %s, t=%s\n- " % (idx,df.iloc[idx]["viewed_by"],df.iloc[idx]["ts"])  + \
           "\n- ".join(df.iloc[idx]["desc"].split(";"))

plt.clf()

plt.scatter(pca_df.iloc[central_situations][0], pca_df.iloc[central_situations][1], s=200,c="black")



c=cursor(hover=True)
c.connect(
    "add", lambda sel: sel.annotation.set_text(labelize(sel.index))
)

plt.scatter(pca_df[df["engaged"] == 1][0], pca_df[df["engaged"] == 1][1],c=label[df["engaged"] == 1],cmap="tab10", marker="*")
plt.scatter(pca_df[df["engaged"] == 0][0], pca_df[df["engaged"] == 0][1],c=label[df["engaged"] == 0],cmap="tab10", marker="o")




In [156]:
df.iloc[central_situations]["desc"]

1390    Jane is talking; Will and Joe are looking at e...
988     Emily and Jane are looking at each other; Will...
884     Will and Joe are looking at each other; Emily ...
709     Joe is talking; Violet is talking; Joe is clos...
706     Will is talking; Joe is talking; Jane is not f...
555     Jane is walking towards Emily; Joe is not far ...
Name: desc, dtype: object

In [168]:
central_situations

array([1390,  988,  884,  709,  706,  555])

# Evolution of social situations

In [324]:
situations = pd.read_csv("situation_1.csv")
situations

engaged viewed_by  actual_ts  \
0         1       Joe        3.0   
1         1     Emily        3.0   
2         1      Will        3.0   
3         0    Violet        3.0   
4         1      Jane        3.0   
5         1       Joe        3.5   
6         1     Emily        3.5   
7         1      Will        3.5   
8         0    Violet        3.5   
9         1      Jane        3.5   
10        1       Joe        4.0   
11        1     Emily        4.0   
12        1      Will        4.0   
13        0    Violet        4.0   
14        1      Jane        4.0   
15        1       Joe        4.5   
16        1     Emily        4.5   
17        1      Will        4.5   
18        0    Violet        4.5   
19        1      Jane        4.5   
20        1       Joe        5.0   
21        1     Emily        5.0   
22        1      Will        5.0   
23        0    Violet        5.0   
24        1      Jane        5.0   
25        1       Joe        5.5   
26        1     Emily        5.5   
27        1      Will        5.5   
28        0    Violet        5.5   
29        1      Jane        5.5   
30        1       Joe        6.0   
31        1     Emily        6.0   
32        1      Will        6.0   
33        0    Violet        6.0   
34        1      Jane        6.0   
35        1       Joe        6.5   
36        1     Emily        6.5   
37        1      Will        6.5   
38        0    Violet        6.5   
39        1      Jane        6.5   
40        1       Joe        7.0   
41        0     Emily        7.0   
42        1      Will        7.0   
43        0    Violet        7.0   
44        0      Jane        7.0   
45        1       Joe        7.5   
46        0     Emily        7.5   
47        1      Will        7.5   
48        0    Violet        7.5   
49        0      Jane        7.5   
50        1       Joe        8.0   
51        0     Emily        8.0   
52        1      Will        8.0   
53        0    Violet        8.0   
54        0      Jane        8.0   
55        1       Joe        8.5   
56        0     Emily        8.5   
57        1      Will        8.5   
58        0    Violet        8.5   
59        0      Jane        8.5   
60        1       Joe        9.0   
61        0     Emily        9.0   
62        1      Will        9.0   
63        0    Violet        9.0   
64        0      Jane        9.0   

                                                t-0.0  \
0   Will and Joe are looking at each other; Emily ...   
1   Jane is not far from Emily; Emily and Jane are...   
2   Will and Joe are looking at each other; Violet...   
3                                    no one is around   
4   Emily and Jane are looking at each other; Emil...   
5   Will and Joe are looking at each other; Emily ...   
6   Will and Joe are looking at each other; Jane i...   
7   Will and Joe are looking at each other; Violet...   
8                                    no one is around   
9   Emily is looking at Jane; Emily is not far fro...   
10  Will and Joe are looking at each other; Emily ...   
11  Will and Joe are looking at each other; Will i...   
12  Will and Joe are looking at each other; Joe is...   
13                                   no one is around   
14  Emily and Jane are looking at each other; Emil...   
15  Will and Joe are looking at each other; Emily ...   
16  Will and Joe are looking at each other; Will i...   
17  Will and Joe are looking at each other; Joe is...   
18                                   no one is around   
19  Emily and Jane are looking at each other; Emil...   
20  Will and Joe are looking at each other; Emily ...   
21  Will and Joe are looking at each other; Will i...   
22  Will and Joe are looking at each other; Joe is...   
23                                   no one is around   
24  Emily and Jane are looking at each other; Emil...   
25  Will and Joe are looking at each other; Will i...   
26  Will and Joe are looking at each other; Will i...   
27  Will and Joe are looking at

In [325]:
# also reverse the order: the 1st row of resulting df is [time_window]s before the timestamp of the last row


sit1=situations.iloc[0:1,3:].transpose().iloc[::-1].rename(columns={0:"desc"})
sit1=pd.merge(sit1, df, on="desc")

sit1



desc  group  engaged  \
0  Emily is looking at Joe; Will is walking towar...      4        0   
1  Emily is looking at Joe; Will is walking towar...      4        0   
2  Will is walking towards Joe; Emily is not far ...      3        0   
3  Will is walking towards Joe; Emily is not far ...      3        0   
4  Will and Joe are looking at each other; Emily ...      2        0   
5  Will and Joe are looking at each other; Emily ...      1        0   
6  Will and Joe are looking at each other; Emily ...      0        1   

  viewed_by   ts         0         1         2         3         4  ...  \
0       Joe  0.5 -0.024636 -0.003566  0.009130  0.019873 -0.022481  ...   
1       Joe  0.5 -0.024636 -0.003566  0.009130  0.019873 -0.022481  ...   
2       Joe  1.5 -0.019964 -0.004463  0.011468  0.032493 -0.019559  ...   
3       Joe  1.5 -0.019964 -0.004463  0.011468  0.032493 -0.019559  ...   
4       Joe  2.0 -0.026705 -0.004962  0.011093  0.023816 -0.021518  ...   
5       Joe  2.5 -0.028806 -0.003917  0.011296  0.027101 -0.027695  ...   
6       Joe  3.0 -0.032531 -0.005525  0.018274  0.023091 -0.020927  ...   

       1526      1527      1528      1529      1530      1531      1532  \
0  0.000360  0.001633  0.002648 -0.008682 -0.015021 -0.017844 -0.002546   
1  0.000360  0.001633  0.002648 -0.008682 -0.015021 -0.017844 -0.002546   
2 -0.005573  0.008635  0.007567 -0.006069 -0.017321 -0.008376 -0.005721   
3 -0.005573  0.008635  0.007567 -0.006069 -0.017321 -0.008376 -0.005721   
4 -0.004250  0.004789  0.002239 -0.007954 -0.013494 -0.012280 -0.001140   
5  0.002139  0.003814  0.003468 -0.006194 -0.007285 -0.007473 -0.001318   
6 -0.002622  0.001248  0.000222 -0.012498 -0.009794 -0.013200 -0.004350   

       1533      1534      1535  
0 -0.014605 -0.009873 -0.034982  
1 -0.014605 -0.009873 -0.034982  
2 -0.020760 -0.017814 -0.026146  
3 -0.020760 -0.017814 -0.026146  
4 -0.015394 -0.018128 -0.032919  
5 -0.018278 -0.016547 -0.041000  
6 -0.016999 -0.018480 -0.035158  

[7 rows x 1541 columns]

In [326]:
pd.DataFrame(cosine_similarity(sit1.iloc[:,idx_embedding:], sit1.iloc[:,idx_embedding:]))

0         1         2         3         4         5         6
0  1.000000  1.000000  0.984643  0.984643  0.983437  0.970087  0.952164
1  1.000000  1.000000  0.984643  0.984643  0.983437  0.970087  0.952164
2  0.984643  0.984643  1.000000  1.000000  0.977532  0.960564  0.944359
3  0.984643  0.984643  1.000000  1.000000  0.977532  0.960564  0.944359
4  0.983437  0.983437  0.977532  0.977532  1.000000  0.987556  0.977508
5  0.970087  0.970087  0.960564  0.960564  0.987556  1.000000  0.981355
6  0.952164  0.952164  0.944359  0.944359  0.977508  0.981355  1.000000

In [327]:
def plot_embedding_path(embeddings):
    #pca = PCA(n_components=2)
    #PCA_result = pca.fit_transform(embeddings)
    #pca_df = pd.DataFrame(PCA_result)
    plt.plot(pca_df[0], pca_df[1],'-o',color="blue")
    for i in range(pca_df.shape[0]):
        plt.annotate(i, (pca_df[0].tolist()[i], pca_df[1].tolist()[i]))


for i in range(len(situations[situations["engaged"] == 1])):

    sit=situations.iloc[i:i+1,3:].transpose().iloc[::-1].rename(columns={i:"desc"})
    sit=pd.merge(sit, df, on="desc")
    plot_embedding_path(sit1.iloc[:,idx_embedding:])


/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py:1402: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  ndim = x[:, None].ndim
/usr/lib/python3/dist-packages/matplotlib/axes/_base.py:276: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  x = x[:, np.newaxis]
/usr/lib/python3/dist-packages/matplotlib/axes/_base.py:278: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  y = y[:, np.newaxis]
/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py:1402: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version

/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py:1402: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  ndim = x[:, None].ndim
/usr/lib/python3/dist-packages/matplotlib/axes/_base.py:276: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  x = x[:, np.newaxis]
/usr/lib/python3/dist-packages/matplotlib/axes/_base.py:278: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  y = y[:, np.newaxis]
/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py:1402: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version

/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py:1402: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  ndim = x[:, None].ndim
/usr/lib/python3/dist-packages/matplotlib/axes/_base.py:276: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  x = x[:, np.newaxis]
/usr/lib/python3/dist-packages/matplotlib/axes/_base.py:278: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  y = y[:, np.newaxis]
/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py:1402: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version

/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py:1402: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  ndim = x[:, None].ndim
/usr/lib/python3/dist-packages/matplotlib/axes/_base.py:276: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  x = x[:, np.newaxis]
/usr/lib/python3/dist-packages/matplotlib/axes/_base.py:278: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version.  Convert to a numpy array before indexing instead.
  y = y[:, np.newaxis]
/usr/lib/python3/dist-packages/matplotlib/cbook/__init__.py:1402: FutureWarning: Support for multi-dimensional indexing (e.g. `obj[:, None]`) is deprecated and will be removed in a future version

In [264]:
pca_df.loc[df['desc'] == sit1.iloc[0]["desc"]]

0         1         2        3         4
59 -0.083003 -0.007743 -0.038595 -0.00997  0.215661

# Querying the models from natural language prompts


In [377]:
from langchain.embeddings import OpenAIEmbeddings
embeddings_model = OpenAIEmbeddings()

In [387]:
desc = "One person face me"
emb = embeddings_model.embed_query(desc)


In [388]:
#sit = closest_situations([emb],together, idx_embedding=4)
sit = closest_situations([emb],df)
print(sit)
pub.publish(df.iloc[sit]["short_code"].values[0])

[452]


In [266]:
together

desc    ts viewed_by_name  \
0   Alice and Oliver are looking at each other; Ol...   3.0         George   
1   Alice and Oliver are looking at each other; Al...   2.5         George   
2   Alice and Oliver are looking at each other; Al...   2.0         George   
3   Alice is not far from me; Oliver is not far fr...   1.5         George   
4   Alice is looking at me; Alice is not far from ...   0.5         George   
5   Alice and I are looking at each other; Alice i...   3.0          Alice   
6   Alice and Oliver are looking at each other; Al...   2.5          Alice   
7   Alice and Oliver are looking at each other; Ol...   2.0          Alice   
8   Alice is looking at Oliver; Alice is not far f...   1.5          Alice   
9   Alice is looking at Oliver; Oliver is passing ...   1.0          Alice   
10                           Alice is not far from me   0.5          Alice   
11  Alice and I are looking at each other; Alice i...   3.0         Phoebe   
12  Alice and I are looking at each other; Alice i...   2.0         Phoebe   
13   Alice is looking at me; Alice is not far from me   1.5         Phoebe   
14  Alice is looking at me; Alice is not far from ...   1.0         Phoebe   
15                                   no one is around   3.0        Matilda   
16  Alice and I are looking at each other; Alice i...   2.5         Oliver   
17  Alice is looking at Oliver; Oliver is looking ...   0.5         Oliver   
18  Alice is looking at Oliver; Oliver is looking ...   0.0         Oliver   
19  Alice and I are looking at each other; Alice i...   3.5         George   
20  Alice and Oliver are looking at each other; Ol...   3.5          Alice   
21  Alice and Oliver are looking at each other; Al...   4.0         George   
22  Alice and Oliver are looking at each other; Al...   4.0          Alice   
23  Alice and I are looking at each other; Alice i...   4.0         Phoebe   
24  Alice and Oliver are looking at each other; Al...   4.5         George   
25  Alice and Oliver are looking at each other; Al...   4.5          Alice   
26  Alice and I are looking at each other; Alice i...   4.5         Oliver   
27  Alice and Oliver are looking at each other; Al...   5.0         George   
28  Alice and Oliver are looking at each other; Al...   5.5         George   
29  Alice and Oliver are looking at each other; Al...   5.5          Alice   
30  Alice and I are looking at each other; Alice i...   5.5         Phoebe   
31  Alice and I are looking at each other; Alice i...   5.5         Oliver   
32  Alice and Oliver are looking at each other; Al...   6.0         George   
33  Alice and Oliver are looking at each other; Al...   6.0          Alice   
34  Alice and I are looking at each other; Alice i...   6.0         Oliver   
35  Alice and I are looking at each other; Alice i...   6.5         George   
36  Alice is close to me; Alice is talking; Oliver...   6.5          Alice   
37  Alice is close to me; Alice is looking at me; ...   6.5         Oliver   
38  Alice and I are looking at each other; Alice i...   7.0         George   
39  Alice is close to me; Alice is talking; Oliver...   7.0          Alice   
40             Alice is close to me; Alice is talking   7.0         Oliver   
41  Alice and I are looking at each other; Alice i...   7.5         George   
42                      Alice is walking away from me   7.5          Alice   
43  Alice and I are looking at each other; Alice i...   8.5         George   
44                                   Alice is talking   9.0         Oliver   
0                                    no one is around   3.0          Alice   
1   Alice and Oliver are looking at each other; Ol...   1.5         George   
2   Alice and Oliver are looking at each other; Ol...   2.5        Matilda   
3   Alice and Oliver are looking at each other; Ol...   0.5        Matilda   
4   Alice and I are looking at each other; Alice i...   3.0         Oliver   
5   Alice and I are looking at each other; Alice i...   2.5         Oli

## Operations on embeddings

In [290]:
emb = together.iloc[131,idx_embedding:] + together.iloc[122,idx_embedding:]
emb

4      -0.029855
5        0.06443
6      -0.006497
7       0.007195
8       0.022101
9      -0.021718
10      0.023271
11      0.043907
12     -0.020658
13     -0.033801
14      0.010253
15     -0.016344
16      0.061417
17      0.021117
18      0.033379
19      -0.03079
20     -0.030807
21      0.004206
22       0.01827
23     -0.004412
24     -0.072739
25     -0.004711
26       0.00388
27     -0.059423
28      0.008153
29     -0.034721
30      0.045253
31      0.010692
32     -0.020997
33     -0.023717
34     -0.045507
35     -0.017513
36     -0.000171
37     -0.011112
38      0.021757
39     -0.013136
40      0.009342
41       -0.0067
42     -0.001739
43     -0.033992
44     -0.048202
45      0.024441
46     -0.048112
47     -0.011133
48     -0.047885
49       0.03113
50      0.019054
51      0.075911
52     -0.040638
53     -0.038605
54     -0.038749
55      0.008271
56      0.023992
57      0.040982
58     -0.036202
59      0.009052
60     -0.008871
61     -0.003651
62     -0.0203

In [291]:
sit = closest_situations([emb],together)
print(sit)
pub.publish(together.iloc[sit]["short_code"].values[0])

[98]


In [289]:
pub.publish(together.iloc[131]["short_code"])

In [286]:
pub.publish(together.iloc[122]["short_code"])